## 5. Idempotents ##
We want to compute the idempotent $E_{\lambda} \in \mathbb{C}[\mathfrak{S}_k]$ associated to the summand $W_{\lambda}(V)$ in the decomposition
$$
V^{\otimes k} = \bigoplus_{\lambda \vdash k}{W_{\lambda}(V)}.
$$
An explicit combinatorial formula for these idempotents was proven by Garsia and Reutenauer [GR89, Theorem 3.2]. It has been implemented in SageMath, see <a href="https://doc.sagemath.org/html/en/reference/algebras/sage/combinat/descent_algebra.html#sage.combinat.descent_algebra.DescentAlgebra.I">here</a>:

In [1]:
def higher_lie_idempotent(la):
    return DescentAlgebra(QQ, la.size()).I().idempotent(la).to_symmetric_group_algebra()

Here are the idempotents for the case $k=3$, see Example 5.1:

In [2]:
k=3
for la in Partitions(k):
    print(la)
    print(higher_lie_idempotent(la))

[3]
1/3*[1, 2, 3] - 1/6*[1, 3, 2] - 1/6*[2, 1, 3] - 1/6*[2, 3, 1] - 1/6*[3, 1, 2] + 1/3*[3, 2, 1]
[2, 1]
1/2*[1, 2, 3] - 1/2*[3, 2, 1]
[1, 1, 1]
1/6*[1, 2, 3] + 1/6*[1, 3, 2] + 1/6*[2, 1, 3] + 1/6*[2, 3, 1] + 1/6*[3, 1, 2] + 1/6*[3, 2, 1]


We now compare the Thrall decomposition with the decomposition of $V^{\otimes k}$ into isotypic components.

The function $\texttt{common_refinement}$ computes the idempotents associated to the coarsest common refinement of the isotypic decomposition and the Thrall decomposition, i.e. to the modules $W_{\lambda}(V)\cap \mathbb{S}_{\mu}(V)^{\oplus m_{\mu}}$. See Example 5.1.

In [3]:
def isotypic_idempotent(mu):
    return SymmetricGroupAlgebra(QQ,mu.size()).central_orthogonal_idempotent(mu)
def common_refinement(k,verbose=True):
    ans={}
    s=SymmetricFunctions(QQ).schur()
    for la in Partitions(k):
        thrallCoefficients=s.gessel_reutenauer(la).monomial_coefficients()     
        E=higher_lie_idempotent(la)
        if verbose:
            print("The Thrall module " + str(la)+":")
        for mu in thrallCoefficients:
            f=E*isotypic_idempotent(mu)
            ans[(la,mu)]=f
            if verbose:
                print("Contains " + str(thrallCoefficients[mu]) + " copies of the Schur module "+str(mu)+". The idempotent is given by")
                print(f)
        if verbose:
            print()
    return ans

In [4]:
common_refinement(3);

The Thrall module [3]:
Contains 1 copies of the Schur module [2, 1]. The idempotent is given by
1/3*[1, 2, 3] - 1/6*[1, 3, 2] - 1/6*[2, 1, 3] - 1/6*[2, 3, 1] - 1/6*[3, 1, 2] + 1/3*[3, 2, 1]

The Thrall module [2, 1]:
Contains 1 copies of the Schur module [1, 1, 1]. The idempotent is given by
1/6*[1, 2, 3] - 1/6*[1, 3, 2] - 1/6*[2, 1, 3] + 1/6*[2, 3, 1] + 1/6*[3, 1, 2] - 1/6*[3, 2, 1]
Contains 1 copies of the Schur module [2, 1]. The idempotent is given by
1/3*[1, 2, 3] + 1/6*[1, 3, 2] + 1/6*[2, 1, 3] - 1/6*[2, 3, 1] - 1/6*[3, 1, 2] - 1/3*[3, 2, 1]

The Thrall module [1, 1, 1]:
Contains 1 copies of the Schur module [3]. The idempotent is given by
1/6*[1, 2, 3] + 1/6*[1, 3, 2] + 1/6*[2, 1, 3] + 1/6*[2, 3, 1] + 1/6*[3, 1, 2] + 1/6*[3, 2, 1]



Finally, we compare the Thrall decomposition with the (noncanonical) decomposition of $V^{\otimes k}$ given by the Young symmetrizers $c_\tau \in \mathbb{C}[\mathfrak{S}_k]$, and with the decomposition given by the 
<q>twisted Young symmetrizers</q> $\tilde{c}_\tau \in \mathbb{C}[\mathfrak{S}_k]$ introduced in Example 5.1.

In [5]:
from sage.combinat.symmetric_group_algebra import a,b, kappa
from sage.combinat.tableau import from_shape_and_word
def young_symmetrizer(T):
    return a(T)*b(T)/kappa(T.shape())
def twisted_young_symmetrizer(T):
    return b(T)*a(T)/kappa(T.shape())
def compare_with_Young_symmetrizers(k,verbose=False):
    commonRefinement=common_refinement(k,verbose=verbose)
    for (la,mu) in commonRefinement:
        print("The Thrall module " + str(la) + " contains a copy of the Schur module " + str(mu) +",")
        E=commonRefinement[(la,mu)]
        for p in Permutations(k):
            found=False
            T=from_shape_and_word(mu,p,convention="English")
            symmetrizer=young_symmetrizer(T)
            if E*symmetrizer==symmetrizer:
                print("given by the Young symmetrizer " + str(T) + ".")
                found = True
                break
            twistedSymmetrizer=twisted_young_symmetrizer(T)
            if E*twistedSymmetrizer==twistedSymmetrizer:
                print("given by the twisted Young symmetrizer " + str(T) + ".")
                found = True
                break
        if not found:
            print("not given by any Young symmetrizer.")

In [6]:
compare_with_Young_symmetrizers(3)

The Thrall module [3] contains a copy of the Schur module [2, 1],
given by the Young symmetrizer [[1, 3], [2]].
The Thrall module [2, 1] contains a copy of the Schur module [1, 1, 1],
given by the Young symmetrizer [[1], [2], [3]].
The Thrall module [2, 1] contains a copy of the Schur module [2, 1],
given by the twisted Young symmetrizer [[1, 2], [3]].
The Thrall module [1, 1, 1] contains a copy of the Schur module [3],
given by the Young symmetrizer [[1, 2, 3]].


In [7]:
compare_with_Young_symmetrizers(4)

The Thrall module [4] contains a copy of the Schur module [2, 1, 1],
not given by any Young symmetrizer.
The Thrall module [4] contains a copy of the Schur module [3, 1],
not given by any Young symmetrizer.
The Thrall module [3, 1] contains a copy of the Schur module [2, 1, 1],
not given by any Young symmetrizer.
The Thrall module [3, 1] contains a copy of the Schur module [3, 1],
not given by any Young symmetrizer.
The Thrall module [3, 1] contains a copy of the Schur module [2, 2],
given by the Young symmetrizer [[1, 3], [2, 4]].
The Thrall module [2, 2] contains a copy of the Schur module [1, 1, 1, 1],
given by the Young symmetrizer [[1], [2], [3], [4]].
The Thrall module [2, 2] contains a copy of the Schur module [2, 2],
given by the twisted Young symmetrizer [[1, 3], [2, 4]].
The Thrall module [2, 1, 1] contains a copy of the Schur module [2, 1, 1],
not given by any Young symmetrizer.
The Thrall module [2, 1, 1] contains a copy of the Schur module [3, 1],
given by the twisted Youn

<h2>Bibliography</h2>
<ul>
<li> [GR89] A. M. Garsia C. Reutenauer. <cite>A decomposition of Solomon’s descent algebra</cite>, Adv.
Math., 77(2):189–262, 1989. </li>
</ul>